# Notebook 01 - Data Cleaning

In [1]:
#Interactive backend
%matplotlib qt

#Essential imports
import hyperspy.api as hs
import numpy as np
import matplotlib.pyplot as plt

### Loading the raw data

In [2]:
dat = hs.load('clmap_type-IIB_HPHT_diamond-spikes_removed.hspy')

In [3]:
#Spikes removal has already been done but can be performed using the following hyperspy widget (see doc)

# dat.spikes_removal_tool()

In [ ]:
#Hyperspectral dataset plot
dat.plot()

### Removing Background fluctuations

Fluctuations of the CCD baseline can be considered as a parabola. Since it is independent from axis
calibration, it is best to remove it before further processing the data.

This can also serve as a basic example of how to apply a model to the data and fit a dataset

In [4]:
#Creation of the model
mod_bkg = dat.create_model()

#Definition of the component, and adding it to the model
poly_2 = hs.model.components1D.Polynomial(2,legacy=False)
mod_bkg.append(poly_2)

#setting of signal range to fit background. We make sure no peak is present in this range
mod_bkg.set_signal_range(205.,225.)
mod_bkg.add_signal_range(261.,268.)

In [5]:
#Background fit. Should take 10-20 sec for the full dataset
mod_bkg.multifit(iterpath='serpentine')

  0%|          | 0/4096 [00:00<?, ?it/s]

In [6]:
#Plotting the results
mod_bkg.plot()

In [7]:
#We reset signal range to obtain the fit function on the whole wavelength axis (optional) and get it as a signal 
mod_bkg.reset_signal_range()
bkg_signal = mod_bkg.as_signal(show_progressbar=False)

In [8]:
#Background removal from the data
dat = (dat-bkg_signal)

In [9]:
#Plotting the map with background corrected
dat.plot()

### Correction of the imaging shift

First step: applying a mask to the data. We remove areas where the panchromatic map is below a threshold --> areas that show no signal

Looking at the panchromatic histogram helps identifying where the limit should be set between dark and light areas

In [10]:
dat.integrate1D(-1).get_histogram().plot()

In [13]:
mask = (dat.integrate1D(-1)<740)

#Last line has a scanning error so we remove it as well
mask.inav[-1,:] = True
#Mask plot
mask.transpose().plot()

Estimation of the shift using cross correlation

In [12]:
shift_map = dat.estimate_shift1D(mask=mask,
                                 interpolate=True,
                                 reference_indices=(34,34),
                                 start=226.,end=251.,
                                 max_shift=10,
                                 parallel=True,
                                 max_workers=4,
                                 show_progressbar=True,)

  0%|          | 0/4096 [00:00<?, ?it/s]

In [14]:
#Creation of a signal2D object containing the shift map.
shift_map_signal = mask._deepcopy_with_new_data(shift_map).transpose()
shift_map_signal.metadata.Signal.quantity = "shift (nm)"
shift_map_signal.plot(cmap = 'jet')

In [15]:
#Saving the shift map
shift_map_signal.save("shift_map.hspy")

Second step: Modelling of the shift with an imaging shift function, and fitting the estimated shift map

In [16]:
#2D fit expression for a plane --> simplest model
imaging_shift_model = hs.model.components2D.Expression(expression="a*x + b*y + c",
                                                       name="Plane2D", 
                                                       add_rotation=False, 
                                                       module="numpy",)

#We add it to the model with some initialisation
planemod = shift_map_signal.create_model()
planemod.append(imaging_shift_model)

#Using the mask to set the signal range
planemod.channel_switches = ~mask.data

#We fit it easy
planemod.fit()

   covar: array([[ 7.15871822e-08, -1.41744247e-10, -7.45925323e-06],
       [-1.41744247e-10,  6.92012777e-08, -7.32351615e-06],
       [-7.45925323e-06, -7.32351615e-06,  1.81657960e-03]])
     fun: array([-0.09638393, -0.10077747, -0.09449437, ..., -0.03678129,
       -0.03049819, -0.03489174])
 message: 'Both actual and predicted relative reductions in the sum of squares\n  are at most 0.000000 and the relative error between two consecutive iterates is at \n  most 0.000000'
    nfev: 13
  status: 3
 success: True
       x: array([-0.02347307,  0.02111312,  0.26284297])

In [17]:
#Getting the results as a signal2D object
planemod.channel_switches[:] = True
shift_plane = planemod.as_signal()
shift_plane.metadata.Signal.quantity = 'shift (nm)'

In [18]:
#Plotting the fit result
shift_plane.plot(cmap = 'jet')

In [20]:
#Displaying a fit residue map
pixsize = dat.axes_manager.signal_axes[-1].scale
residue = (shift_plane-shift_map_signal)/pixsize
residue.metadata.Signal.quantity = "Shift (# of CCD Pixels)"
residue.plot(cmap='Spectral_r')

Resampling the data on the corrected axis

In [21]:
dat.shift1D(shift_array=shift_plane.data, interpolation_method='quadratic')

  0%|          | 0/4096 [00:00<?, ?it/s]

*At this point you can call estimate_shift again to check that the plane is corrected*

In [22]:
tmp = dat.estimate_shift1D(mask=mask,
                                 interpolate=True,
                                 reference_indices=(34,34),
                                 start=226.,end=251.,
                                 max_shift=10,
                                 parallel=True,
                                 max_workers=4,)
pss = mask._deepcopy_with_new_data(tmp).transpose()
pss.metadata.Signal.quantity = "shift (nm)"

  0%|          | 0/4096 [00:00<?, ?it/s]

In [24]:
pss.plot(cmap = 'jet')

### Saving the fully corrected map

In [25]:
#At this stage, we can also crop out the last column which obviously has an artefact
dat = dat.inav[:-1,:]

In [26]:
dat.save("clmap_IIB-HPHT-diamond_cleaned.hspy")

In [27]:
plt.close('all')